In [ ]:
'''
import os
from konlpy import utils


javadir = '%s%sjava' % (utils.installpath, os.sep)
args = [javadir, os.sep]
folder_suffix = ['{0}{1}open-korean-text-2.1.0.jar']
classpath = [f.format(*args) for f in folder_suffix]

print('javadir  : {}'.format(javadir))
print('os.sep   : {}'.format(os.sep))
print('classpath: {}'.format(classpath[0]))
'''

In [1]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfTransformer, CountVectorizer
from sklearn.linear_model import LogisticRegression
#from sklearn.model_selection import train_test_split

In [2]:
disease = pd.read_excel("./data/disease.xlsx", engine="openpyxl")
disease.head()

질병명   
0                       근감소증(Sarcopenia)  \
1                       코로나-19(COVID-19)   
2  용혈성 요독 증후군(Hemolytic Uremic Syndrome)   
3                  단순 포진(Herpes Simplex)   
4                   약물 발진(Drug Eruption)   

                                               증상키워드   
0                         보행이상, 근력 약화, 피로감, 하지의 근력약화  \
1               가래, 기침, 목의 통증, 근육통, 피로감, 열, 두통, 호흡곤란   
2  멍, 빈혈, 열, 황달, 혈뇨, 신부전, 전신 부종, 간비대, 복부 통증, 자반증,...   
3                                       작열감, 물집, 소양감   
4                                                 발진   

                                                관련질환   
0                                       노화, 골다공증, 노쇠  \
1  상기도 감염, 중동 호흡기 증후군(MERS), 중증 급성 호흡기 증후군, 인플루엔자...   
2  후천성 면역결핍증, 폰빌레브란트병, 면역혈소판감소증, 식중독, 항인지질 항체 증후군...   
3                      대상포진, 단순 포진성 뇌염, 헤르페스 바이러스 감염   
4                                            약물 알레르기   

                               진료과   
0                             노년내과  \
1                      감염내과, 호흡기내과   
2  감염내과, 소화기내과, 신장내과, 소아신장과, 소아감염과   
3                              피부과   
4                              피부과   

                                                  정의   
0  근감소증은 나이가 많아지면서 근육의 양, 근력, 근 기능이 모두 감소하는 질환을 의...  \
1  중국 우한에서 발생한 폐렴은 신종 코로나 바이러스인 ‘2019-nCoV' 가 원인으...   
2  용혈성 요독 증후군은 4세 이하 영유아나 고령의 환자에게 급성 신부전을 일으키는 질...   
3  단순 포진(Herpes simplex)은 헤르페스 바이러스의 일종인 단순 포진 바이...   
4  약물에 의한 이상반응으로 피부에 발진이 생긴 것을 약물 발진, 또는 약진이라고 부릅니다.   

                                                  원인   
0  근감소증의 원인은 개인마다 다르지만, 가장 흔한 원인은 단백질 섭취 저하, 운동량 ...  \
1  국제보건기구(WHO)에 따르면 우한에서 발생한 새로운 코로나 바이러스의 확산은 동물...   
2  용혈성 요독 증후군의 원인은 크게 감염, 유전, 약물 등으로 생각할 수 있습니다. ...   
3  단순포진은 성교를 통해 헤르페스 바이러스에 감염되어 발생하는 질환이다. 헤르페스 바...   
4  어떠한 약물이 병변을 흔히 유발하는지 알아두면 진단과 원인 규명에 도움이 됩니다.\...   

                                                증상설명   
0  근감소증의 증상으로는 근력 저하, 하지 무력감, 피곤감이 있습니다. 근육량과 근력은...  \
1  코로나-19에 감염되면 2~3일에서 최장 2주 정도 잠복기를 거쳤다가 다양한 증상이...   
2  설사 연관형에서는 설사나 혈변이 나타납니다. 복통, 발열, 구토 등의 대장염 증상을...   
3  단순 포진에 걸리면 임상적으로 피부 또는 점막에 홍반과 함께 군집을 이루는 작은 물...   
4  증상은 매우 다양하여 다른 피부질환과의 감별을 필요로 합니다.\n \n바이러스나 세...   

                                                  진단   
0  근감소증은 근육량, 근력, 근 기능을 측정하여 진단합니다. 연령과 성별뿐만 아니라 ...  \
1  환자와 밀접하게 접촉한 사람이 14일 이내에 37.5도 이상의 발열, 기침, 인후통...   
2  혈액 검사상 용혈성 빈혈, 혈소판 감소, 신 기능의 이상을 확인할 수 있습니다. 소...   
3  단순 포진은 대개 특징적인 임상 증상으로 쉽게 진단할 수 있습니다. 간혹 바이러스 ...   
4  1. 환자의 병력 청취\n약물을 사용한 시기와 피부 병변과의 상관관계를 알기 위해 ...   

                                                  치료  
0  근감소증이 나타나기 전에 근력 저하가 먼저 발생하는 경우가 많습니다. 근력 저하나 ...  
1  현재까지 코로나-19에 대해 정립된 치료법은 없습니다. 증상에 따른 약제를 사용하고...  
2  용혈성 요독 증후군 환자는 신부전이 발생하므로 수분, 전해질, 산-염기 이상을 교정...  
3  단순 포진 바이러스 감염은 대부분 치료할 필요가 없으며, 병변을 깨끗하고 건조하게 ...  
4  병변의 치료는 우선 의심되는 약물을 가능한 모두 끊거나 다른 약물로 대체합니다. \...

In [3]:
disease1 = disease[['질병명']]
disease1.head()

질병명
0                       근감소증(Sarcopenia)
1                       코로나-19(COVID-19)
2  용혈성 요독 증후군(Hemolytic Uremic Syndrome)
3                  단순 포진(Herpes Simplex)
4                   약물 발진(Drug Eruption)

In [4]:
disease1.tail()

질병명
730    게실 질환(Diverticular disease)
731  대장의 양성 종양(Benign colon tumor)
732            항문 누공(Anal fistula)
733     항문 주위 농양(Perianal abscess)
734            항문 열구(Anal fissure)

In [5]:
disease1['키워드'] = disease['증상키워드'] + ', ' + disease['관련질환'] + ', ' + disease['정의'] + ', ' + disease['증상설명']
disease1.head()

C:\Users\namyo\AppData\Local\Temp\ipykernel_35484\2580576481.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  disease1['키워드'] = disease['증상키워드'] + ', ' + disease['관련질환'] + ', ' + disease['정의'] + ', ' + disease['증상설명']


질병명   
0                       근감소증(Sarcopenia)  \
1                       코로나-19(COVID-19)   
2  용혈성 요독 증후군(Hemolytic Uremic Syndrome)   
3                  단순 포진(Herpes Simplex)   
4                   약물 발진(Drug Eruption)   

                                                 키워드  
0  보행이상, 근력 약화, 피로감, 하지의 근력약화, 노화, 골다공증, 노쇠, 근감소증...  
1  가래, 기침, 목의 통증, 근육통, 피로감, 열, 두통, 호흡곤란, 상기도 감염, ...  
2  멍, 빈혈, 열, 황달, 혈뇨, 신부전, 전신 부종, 간비대, 복부 통증, 자반증,...  
3  작열감, 물집, 소양감, 대상포진, 단순 포진성 뇌염, 헤르페스 바이러스 감염, 단...  
4  발진, 약물 알레르기, 약물에 의한 이상반응으로 피부에 발진이 생긴 것을 약물 발진...

In [6]:
for i in range(0, 735):
    disease1.loc[i,'키워드'] = disease1.loc[i,'키워드'].replace(',','')

#print(disease1[['키워드']].head())
#print(disease1[['키워드']].tail())
disease1.head()

질병명   
0                       근감소증(Sarcopenia)  \
1                       코로나-19(COVID-19)   
2  용혈성 요독 증후군(Hemolytic Uremic Syndrome)   
3                  단순 포진(Herpes Simplex)   
4                   약물 발진(Drug Eruption)   

                                                 키워드  
0  보행이상 근력 약화 피로감 하지의 근력약화 노화 골다공증 노쇠 근감소증은 나이가 많...  
1  가래 기침 목의 통증 근육통 피로감 열 두통 호흡곤란 상기도 감염 중동 호흡기 증후...  
2  멍 빈혈 열 황달 혈뇨 신부전 전신 부종 간비대 복부 통증 자반증 설사 고혈압 혈변...  
3  작열감 물집 소양감 대상포진 단순 포진성 뇌염 헤르페스 바이러스 감염 단순 포진(H...  
4  발진 약물 알레르기 약물에 의한 이상반응으로 피부에 발진이 생긴 것을 약물 발진 또...

In [7]:
from pykospacing import Spacing  # 띄어쓰기가 되어있지 않은 문장을 올바르게 변환해준다.
spacing = Spacing()

for i in range(0, 735):
    disease1.loc[i, '키워드'] = spacing(disease1.loc[i, '키워드'])

disease1.head()

질병명   
0                       근감소증(Sarcopenia)  \
1                       코로나-19(COVID-19)   
2  용혈성 요독 증후군(Hemolytic Uremic Syndrome)   
3                  단순 포진(Herpes Simplex)   
4                   약물 발진(Drug Eruption)   

                                                 키워드  
0  보행 이상 근력 약화 피로감 하지의 근력 약화 노화 골다공증 노쇠 근감소증은 나이가...  
1  가래 기침 목의 통증 근육통 피로감 열 두통 호흡곤란 상기도 감염 중동 호흡기 증후...  
2  멍 빈혈 열 황달 혈뇨 신부전 전신 부종 간 비대 복부 통증 자반증 설사 고혈압 혈...  
3  작열감 물집 소양감 대상포진 단순 포진성 뇌염 헤르페스 바이러스 감염 단순 포진(H...  
4  발진 약물 알레르기 약물에 의 한 이 상반응으로 피부에 발진이 생긴 것을 약물 발진...

In [8]:
from konlpy.tag import Okt
t = Okt()

print("명사만 추출 : \n{}".format(t.morphs(disease1['키워드'][0], stem=True, norm=True)))
print("\n품사 태깅 추출 : \n{}".format(t.pos(disease1['키워드'][0], stem=True, norm=True)))

명사만 추출 : 
['보행', '이상', '근력', '약화', '피로', '감', '하다', '근력', '약화', '노화', '골다공증', '노쇠', '근', '감소', '증', '은', '나이', '가', '많아지다', '근육', '의', '양', '근력', '근', '기능', '이', '모두', '감소', '하다', '질환', '을', '의', '밉다', '하다', '.', '근', '감소', '증', '의', '증상', '으로는', '근력', '저하', '하다', '무력감', '피곤', '감', '이', '있다', '.', '근', '육', '량', '과', '근력', '은', '나이', '가', '들다', '자연', '스럽게', '줄어들다', '근', '감소', '증', '은', '나이', '나', '성별', '등', '을', '감안', '하다', '근', '육', '량', '과', '근력', '이', '지나치다', '줄어들다', '신체', '기능', '이', '떨어지다', '건강', '상의', '위험', '이나', '사망률', '이', '증가', '하다', '.', '근', '감소', '증', '환자', '는', '걸음걸이', '가', '늦어지다', '근', '지구력', '이', '떨어지다', '일', '상', '생활', '이', '어렵다', '다른', '사람', '의', '도움', '이', '자주', '필요하다', '되다', '.', '또', '골다공증', '낙상', '골절', '이', '쉬다', '발생', '하다', '.', '근육', '의', '혈액', '및', '호르몬', '완충', '작용', '이', '줄다', '들다', '기초', '대', '사량', '이', '감소', '하고', '만성', '질환', '조절', '이', '어렵다', '되다', '당뇨병', '과', '심', '혈관', '질환', '이', '쉬다', '악화', '되다', '수', '있다', '습', '니', '다', '.']

품사 태깅 추출 : 
[('보행', 'Noun'),

In [9]:
# 불용어 리스트 : 664개
# 참고링크 : https://www.ranks.nl/stopwords/korean, https://bab2min.tistory.com/544, 
stopword_file = pd.read_excel('stopword.xlsx', engine='openpyxl')

a = []
for i in range(len(stopword_file.index)):
    a.append(stopword_file.iloc[i, 0])

stopword = list(set(a))
print(stopword)
print(len(stopword))

['여부', '앞', '콸콸', '아니라면', '것들', '차라리', '지금', '할줄알다', '그위에', '아이쿠', '그렇지 않다면', '이상', '이로 인하여', '로부터', '로 인하여', '다섯', '윙윙', '원', '대로 하다', '어떠한', '삼', '를', '하겠는가', '의지하여', '의거하여', '언젠가', '이런', '구토하다', '남들', '이쪽', '번', '통하여', '정도', '말하', '할 힘이 있다', '얼마', '다소', '예컨대', '크', '부터', '이용하여', '그때', '개', '이었다', '고로', '참나', '설사', '하게하다', '하물며', '하', '어기여차', '해요', '저것만큼', '게다가', '까지도', '한 이유는', '등등', '월', '툭', '이 밖에', '허', '겸사겸사', '그래', '하기보다는', '소생', '과', '일단', '응당', '할지언정', '잘', '혹은', '그러', '대해서', '이와같다면', '지', '말하자면', '야', '하지만', '왜냐하면', '자신', '이', '데', '저것', '약간', '해야한다', '이만큼', '한마디', '매', '요컨대', '각각', '자', '임에 틀림없다', '딩동', '얼마큼', '칠', '할 따름이다', '기준으로', '몇', '더군다나', '잇따라', '등', '얼마나', '그', '엉엉', '에서', '아래윗', '된이상', '사람', '모', '갖고말하자면', '다음', '하나', '형식으로 쓰여', '줄은모른다', '운운', '만이 아니다', '고려하면', '그렇지 않으면', '연관되다', '겨우', '너', '어느쪽', '졸졸', '보는데서', '생각한대로', '뿐이다', '솨', '그만이다', '여덟', '봐', '하기 위하여', '어이', '조금', '펄렁', '대해 말하자면', '응', '저희', '일곱', '바꾸어말하면', '따라', '향하여', '여섯', '어느 년도', '보이', '타인', '싶', '관한',

In [21]:
if '붙이다' in stopword :
    print('true')
else:
    print('false')

false


In [10]:
keyword = []
for token, pos in t.pos(disease1['키워드'][0], stem=True, norm=True):
    if pos in ['Noun', 'Adjective', 'Adverb']:  # 명사, 형용사, 부사인 것 만 추출
        keyword.append(token)

#print(list(set(keyword)))
#key_list = []
#for lk in list(set(keyword)):
#    if lk not in stopword:
#        key_list.append(lk)
#print(key_list)

key_list = [lk for lk in list(set(keyword)) if lk not in stopword and len(lk) > 1]
print(key_list)

['감안', '노화', '악화', '사망률', '작용', '발생', '근력', '질환', '나이', '피곤', '어렵다', '낙상', '당뇨병', '저하', '완충', '상의', '환자', '걸음걸이', '호르몬', '기능', '보행', '약화', '생활', '도움', '사량', '피로', '노쇠', '무력감', '혈관', '위험', '만성', '혈액', '감소', '조절', '증상', '밉다', '자연', '건강', '지구력', '필요하다', '골절', '기초', '근육', '신체', '성별', '자주', '증가', '골다공증']


In [11]:
df = pd.DataFrame(columns=['토큰키워드'])
idx = 0

for i in range(len(disease1)):
    keyword = []
    for token, pos in t.pos(disease1['키워드'][i], stem=True, norm=True):
        if pos in ['Noun', 'Verb', 'Adjective', 'Adverb']:
            if token not in stopword:
                keyword.append(token)
    new_keyword = list(set(keyword))
    new_key_list = [lk for lk in new_keyword if lk not in stopword and len(lk) > 1]
    
    df.loc[idx] = [new_key_list]
    idx+=1
    print(new_key_list)

['감안', '노화', '악화', '사망률', '작용', '발생', '근력', '질환', '하다', '나이', '피곤', '쉬다', '떨어지다', '어렵다', '낙상', '들다', '저하', '당뇨병', '줄어들다', '완충', '상의', '늦어지다', '환자', '걸음걸이', '되다', '호르몬', '기능', '보행', '도움', '약화', '사량', '생활', '피로', '노쇠', '무력감', '혈관', '위험', '만성', '혈액', '감소', '증가', '조절', '증상', '밉다', '많아지다', '자연', '건강', '지구력', '필요하다', '골절', '기초', '근육', '신체', '성별', '자주', '지나치다', '골다공증', '줄다']
['원인', '감기', '둘레', '질환', '신종', '후통', '달라', '호흡기', '수도', '되다', '따르다', '중증', '중동', '분류', '심하다', '잠복기', '상기', '성질', '무기', '하다', '로나', '방사', '되어다', '알려지다', '중국', '모양', '주로', '나타나다', '퍼지다', '돼다', '이다', '증상', '사망', '처음', '코로나', '현미경', '가래', '손상', '감염', '두통', '호흡부전', '피로', '이름', '일으키다', '근육통', '명명', '동물', '증후군', '붙이다', '통증', '관찰', '발생', '메르스', '다양하다', '인플루엔자', '고열', '형태', '확인', '인체', '의미', '오다', '바이러스', '호흡', '기침', '이르다', '곤란', '가다', '급성', '사스', '폐렴', '거치다', '우한']
['구토', '집단', '감기', '질환', '결핍', '먹다', '들다', '불리다', '되다', '황달', '유형', '혈압', '동반', '항체', '혈변', '면역', '낭창', '하다', '식중독', '유아', '전신', '특징', '미국', '지다', '세균', '자반증', '나타나다',

In [12]:
df

토큰키워드
0    [감안, 노화, 악화, 사망률, 작용, 발생, 근력, 질환, 하다, 나이, 피곤, ...
1    [원인, 감기, 둘레, 질환, 신종, 후통, 달라, 호흡기, 수도, 되다, 따르다,...
2    [구토, 집단, 감기, 질환, 결핍, 먹다, 들다, 불리다, 되다, 황달, 유형, ...
3    [원인, 질환, 여러, 나뉘다, 가렵거, 상태, 재발, 없다, 농포, 되다, 사라지...
4    [생기다, 원인, 갑자기, 지니다, 다양하다, 질환, 하다, 발진, 두드러기, 천포...
..                                                 ...
730  [수술, 지혈, 질환, 자다, 여러, 돌출, 호소, 변화, 되다, 따르다, 메켈, ...
731  [상대, 질환, 자다, 주변, 돌출, 묻다, 소아, 소견, 없다, 막다, 자라나다,...
732  [질환, 지속, 주변, 여러, 묻다, 느끼다, 누공, 생기지, 열다, 되다, 되풀이...
733  [느껴지다, 인하다, 생기다, 구멍, 작용, 이러하다, 질환, 하다, 농양, 기도,...
734  [느껴지다, 조그맣다, 질환, 자다, 묻다, 살이, 화장지, 누공, 열다, 되다, ...

[735 rows x 1 columns]

In [13]:
disease1 = pd.concat([disease1['질병명'], df], axis=1)
disease1

질병명   
0                         근감소증(Sarcopenia)  \
1                         코로나-19(COVID-19)   
2    용혈성 요독 증후군(Hemolytic Uremic Syndrome)   
3                    단순 포진(Herpes Simplex)   
4                     약물 발진(Drug Eruption)   
..                                     ...   
730            게실 질환(Diverticular disease)   
731          대장의 양성 종양(Benign colon tumor)   
732                    항문 누공(Anal fistula)   
733             항문 주위 농양(Perianal abscess)   
734                    항문 열구(Anal fissure)   

                                                 토큰키워드  
0    [감안, 노화, 악화, 사망률, 작용, 발생, 근력, 질환, 하다, 나이, 피곤, ...  
1    [원인, 감기, 둘레, 질환, 신종, 후통, 달라, 호흡기, 수도, 되다, 따르다,...  
2    [구토, 집단, 감기, 질환, 결핍, 먹다, 들다, 불리다, 되다, 황달, 유형, ...  
3    [원인, 질환, 여러, 나뉘다, 가렵거, 상태, 재발, 없다, 농포, 되다, 사라지...  
4    [생기다, 원인, 갑자기, 지니다, 다양하다, 질환, 하다, 발진, 두드러기, 천포...  
..                                                 ...  
730  [수술, 지혈, 질환, 자다, 여러, 돌출, 호소, 변화, 되다, 따르다, 메켈, ...  
731  [상대, 질환, 자다, 주변, 돌출, 묻다, 소아, 소견, 없다, 막다, 자라나다,...  
732  [질환, 지속, 주변, 여러, 묻다, 느끼다, 누공, 생기지, 열다, 되다, 되풀이...  
733  [느껴지다, 인하다, 생기다, 구멍, 작용, 이러하다, 질환, 하다, 농양, 기도,...  
734  [느껴지다, 조그맣다, 질환, 자다, 묻다, 살이, 화장지, 누공, 열다, 되다, ...  

[735 rows x 2 columns]

In [14]:
disease1.to_csv('token_disease.csv', encoding='utf-8-sig', index=False)

In [15]:
token_disease = pd.read_csv('token_disease.csv')
token_disease

질병명   
0                         근감소증(Sarcopenia)  \
1                         코로나-19(COVID-19)   
2    용혈성 요독 증후군(Hemolytic Uremic Syndrome)   
3                    단순 포진(Herpes Simplex)   
4                     약물 발진(Drug Eruption)   
..                                     ...   
730            게실 질환(Diverticular disease)   
731          대장의 양성 종양(Benign colon tumor)   
732                    항문 누공(Anal fistula)   
733             항문 주위 농양(Perianal abscess)   
734                    항문 열구(Anal fissure)   

                                                 토큰키워드  
0    감안 노화 악화 사망률 작용 발생 근력 질환 하다 나이 피곤 쉬다 떨어지다 어렵다 ...  
1    원인 감기 둘레 질환 신종 후통 달라 호흡기 수도 되다 따르다 중증 중동 분류 심하...  
2    구토 집단 감기 질환 결핍 먹다 들다 불리다 되다 황달 유형 혈압 동반 항체 혈변 ...  
3    원인 질환 여러 나뉘다 가렵거 상태 재발 없다 농포 되다 사라지다 드물다 물집 형성...  
4    생기다 원인 갑자기 지니다 다양하다 질환 하다 발진 두드러기 천포창 투약 감염 발행...  
..                                                 ...  
730  수술 지혈 질환 자다 여러 돌출 호소 변화 되다 따르다 메켈 대량 결장 반복 변비 ...  
731  상대 질환 자다 주변 돌출 묻다 소아 소견 없다 막다 자라나다 눌립니 변화 되다 거...  
732  질환 지속 주변 여러 묻다 느끼다 누공 생기지 열다 되다 되풀이 통해 진물 터널 배...  
733  느껴지다 인하다 생기다 구멍 작용 이러하다 질환 하다 농양 기도 나오다 일어나다 과...  
734  느껴지다 조그맣다 질환 자다 묻다 살이 화장지 누공 열다 되다 반복 변비 심하다 궤...  

[735 rows x 2 columns]

In [166]:
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split

# 데이터셋 로드
token_disease = pd.read_csv('token_disease.csv')

# CountVectorizer와 TfidfTransformer를 사용하여 증상 벡터화
vectorizer = CountVectorizer()
transformer = TfidfTransformer()

symptoms = token_disease['토큰키워드'].values
symptom_vectors = vectorizer.fit_transform(symptoms)
symptom_tfidf = transformer.fit_transform(symptom_vectors)

# 다항 로지스틱 회귀 분석 모델 학습
model = LogisticRegression(multi_class='multinomial', solver='lbfgs')
model.fit(symptom_tfidf, token_disease['질병명'])

# 테스트 데이터셋 분리
X_train, X_test, y_train, y_test = train_test_split(token_disease['토큰키워드'], token_disease['질병명'], test_size=0.2, random_state=42)

# 테스트 데이터셋 벡터화
X_test_vectors = vectorizer.transform(X_test)
X_test_tfidf = transformer.transform(X_test_vectors)

# 다항 로지스틱 회귀 분석 모델을 사용하여 질병 예측
predicted_diseases = model.predict(X_test_tfidf)

# 예측된 질병 출력
print('예측된 질병:')
for i, disease in enumerate(predicted_diseases):
    print(f'{i+1}. {disease}')

# 예측한 질병의 확률 출력
predicted_probabilities = model.predict_proba(X_test_tfidf)
print('예측한 질병의 확률:')
for i, probabilities in enumerate(predicted_probabilities):
    print(f'{i+1}. {dict(zip(model.classes_, probabilities))}')

# 정확도, 정밀도, 재현율, F1 스코어 출력
print('평가 결과:')
print(classification_report(y_test, predicted_diseases))

예측된 질병:
1. 심내막염(Endocarditis)
2. 심방 조동(Atrial Flutter)
3. 전신 홍반성 낭창(Systemic lupus erythematosus)
4. 사마귀(Wart)
5. 반월판 연골손상(Tear of meniscus)
6. 위궤양(Gastric ulcer)
7. 중심장액성 맥락망막병증(Central Serous ChorioRetinopathy)
8. 아토피성 피부염(Atopic dermatitis)
9. 후두암(Larynx  cancer)
10. 쿠싱 증후군(Cushings syndrome)
11. 당뇨망막병증(Diabetic retinopathy)
12. 수족냉증(Coldness of hands and feet)
13. 인슐린 의존성 당뇨병(Insulin-dependent diabetes mellitus)
14. 비만(Obesity)
15. 듀피트렌 구축(Dupuytrens contracture)
16. 박테리아성 뇌수막염(Bacterial meningitis)
17. 베이커 낭종(Bakers cyst)
18. 담낭 용종(GB polyp)
19. 장티푸스(typhoid fever)
20. 신장의 신생물(Neoplasm of the kidney)
21. 스티븐 존슨 증후군(Stevens Johnson syndrome)
22. 납 중독(Lead Poisoning)
23. 이루증(Otorrhea)
24. 내연골종(Enchondroma)
25. 당뇨병성 족부 질환(DM foot ulcer)
26. 대상포진 후 신경통(Postzoster neuralgia)
27. 골괴사(Osteonecrosis)
28. 기미(Melasma)
29. 노로바이러스 장염(Norovirus Gastroenteritis)
30. 순수적혈구무형성(Pure red cell aplasia)
31. 감염성 근육염(Infective myositis)
32. 패혈증(Sepsis)
33. 수부 습진(Hand Eczema)
34. 방선균증(Actinomycosis)
35.

In [168]:
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.linear_model import LogisticRegression
import numpy as np

# 데이터셋 로드
token_disease = pd.read_csv('token_disease.csv')

# CountVectorizer와 TfidfTransformer를 사용하여 증상 벡터화
vectorizer = CountVectorizer()
transformer = TfidfTransformer()

symptoms = token_disease['토큰키워드'].values
symptom_vectors = vectorizer.fit_transform(symptoms)
symptom_tfidf = transformer.fit_transform(symptom_vectors)

# 다항 로지스틱 회귀 분석 모델 학습
model = LogisticRegression(multi_class='multinomial', solver='lbfgs')
model.fit(symptom_tfidf, token_disease['질병명'])

# 미리 정해진 증상 목록
available_symptoms = ['기침', '콧물', '인후통', '호흡곤란', '가슴통증', '발열', '천식발작', '가려움증', '발진', '붓기', '복통', '구토', '속쓰림']

# 사용자로부터 증상 선택 받기
print('다음 중 해당하는 증상을 선택하세요 (여러 개 선택 가능, 끝내려면 엔터):')
for i, symptom in enumerate(available_symptoms):
    print(f'{i+1}. {symptom}')

user_input = input()
user_symptoms = [available_symptoms[int(i)-1] for i in user_input.split(',')]

# 선택된 증상을 벡터화하여 예측에 사용
user_vector = vectorizer.transform([' '.join(user_symptoms)])
user_tfidf = transformer.transform(user_vector)

# 다항 로지스틱 회귀 분석 모델을 사용하여 질병 예측
predicted_probabilities = model.predict_proba(user_tfidf)[0]

# 상위 5개의 질병 출력
top_5_indices = np.argsort(predicted_probabilities)[::-1][:5]
print('상위 5개의 질병:')
for i, index in enumerate(top_5_indices):
    print(f'{i+1}. {model.classes_[index]} ({predicted_probabilities[index]:.2f})')

다음 중 해당하는 증상을 선택하세요 (여러 개 선택 가능, 끝내려면 엔터):
1. 기침
2. 콧물
3. 인후통
4. 호흡곤란
5. 가슴통증
6. 발열
7. 천식발작
8. 가려움증
9. 발진
10. 붓기
11. 복통
12. 구토
13. 속쓰림
상위 5개의 질병:
1. 폐 전이(Lung Metastasis) (0.00)
2. 폐부종(Pulmonary edema) (0.00)
3. 폐결핵(Pulmonary tuberculosis) (0.00)
4. 진폐증(Pneumoconiosis) (0.00)
5. 폐암(Lung cancer) (0.00)


In [169]:
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.linear_model import LogisticRegression
from konlpy.tag import Okt

# 데이터셋 로드
token_disease = pd.read_csv('token_disease.csv')

# CountVectorizer와 TfidfTransformer를 사용하여 증상 벡터화
vectorizer = CountVectorizer()
transformer = TfidfTransformer()

symptoms = token_disease['토큰키워드'].values
symptom_vectors = vectorizer.fit_transform(symptoms)
symptom_tfidf = transformer.fit_transform(symptom_vectors)

# 다항 로지스틱 회귀 분석 모델 학습
model = LogisticRegression(multi_class='multinomial', solver='lbfgs')
model.fit(symptom_tfidf, token_disease['질병명'])

# 사용자로부터 증상 입력 받기
user_input = input('증상을 입력하세요: ')

# 입력된 증상을 토큰화하고 정규화하여 예측에 사용
okt = Okt()
user_tokens = okt.morphs(user_input)
user_normalized = [token for token in user_tokens if len(token) > 1]
user_vector = vectorizer.transform([' '.join(user_normalized)])
user_tfidf = transformer.transform(user_vector)

# 다항 로지스틱 회귀 분석 모델을 사용하여 질병 예측
#predicted_disease = model.predict(user_tfidf)
predicted_probabilities = model.predict_proba(user_tfidf)[0]

# 예측된 질병 출력
#print('예측된 질병:', predicted_disease[0])

예측된 질병: 냉방병(Air-conditioningitis)


### 로지스틱회귀

In [31]:
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.linear_model import LogisticRegression
from konlpy.tag import Okt
import numpy as np

# 데이터셋 로드
token_disease = pd.read_csv('token_disease.csv')

# CountVectorizer와 TfidfTransformer를 사용하여 증상 벡터화
cv = CountVectorizer()
tfidf = TfidfTransformer()

symptoms = token_disease['토큰키워드'].values
symptom_vectors = cv.fit_transform(symptoms)
symptom_tfidf = tfidf.fit_transform(symptom_vectors)

# 다항 로지스틱 회귀 분석 모델 학습
model = LogisticRegression(multi_class='multinomial', solver='lbfgs')
model.fit(symptom_tfidf, token_disease['질병명'])

# 사용자로부터 증상 입력 받기
question = input("증상을 입력하세요 : ")

# 입력된 증상을 토큰화하고 정규화하여 예측에 사용
t = Okt()
q_list = [token for token, pos in t.pos(question, stem=True, norm=True) if pos in ['Noun', 'Adjective', 'Adverb']]
qustion_key_list = [lk for lk in list(set(q_list)) if lk not in stopword and len(lk) > 1]
#print(qustion_key_list)
user_vector = cv.transform([' '.join(qustion_key_list)])
user_tfidf = tfidf.transform(user_vector)

# 다항 로지스틱 회귀 분석 모델을 사용하여 질병 예측
#predicted_probabilities = model.predict_proba(user_tfidf)[0]

# 상위 10개의 질병 출력
top_10_indices = np.argsort(predicted_probabilities)[::-1][:10]
print('상위 10개의 질병:')
for i, index in enumerate(top_10_indices):
    print(f'{i+1}. {model.classes_[index]}')  # ({predicted_probabilities[index]:.4f})

상위 10개의 질병:
1. 심방 세동(Atrial fibrillation) (0.0015)
2. 냉방병(Air-conditioningitis) (0.0015)
3. 메니에르병(Meniere's disease) (0.0015)
4. 용혈성 요독 증후군(Hemolytic Uremic Syndrome) (0.0015)
5. 고산병(Mountain sickness) (0.0015)
6. 땀띠(Miliaria) (0.0015)
7. 갑상선기능항진증(Hyperthyroidism) (0.0015)
8. 익상편(Pterygium) (0.0014)
9. 췌장암(Pancreatic cancer) (0.0014)
10. 고관절 이형성증(DDH (developmental dysplasia of the hip)) (0.0014)
11. 대퇴골두 무혈관성 괴사(AVN of hip(femoral head)) (0.0014)
12. 뎅기열(Dengue fever) (0.0014)
13. 만성 부비동염(Chronic rhinosinusitis) (0.0014)
14. 위말트 림프종 (Gastric MALT lymphoma) (0.0014)
15. 이석증(Benign paroxysmal vertigo) (0.0014)
16. 동결견(Frozen shoulder) (0.0014)
17. 발모벽(Trichotillomania) (0.0014)
18. 현훈(Vertigo) (0.0014)
19. 십이지장염(Duodenitis) (0.0014)
20. 척추병증(Spondylopathies) (0.0014)
21. 관절와순 파열(Labral tear) (0.0014)
22. 독성 간염(Toxic hepatitis) (0.0014)
23. 두개골 골절(Skull Fracture) (0.0014)
24. 춘곤증(spring fatigue) (0.0014)
25. 상대정맥 증후군(Superior vena cava Syndrome) (0.0014)
26. 스파르가눔증(Sparganosis) (0.0014)


### 랜덤포레스트

In [32]:
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.ensemble import RandomForestClassifier
from konlpy.tag import Okt
import numpy as np

# 데이터셋 로드
token_disease = pd.read_csv('token_disease.csv')

# CountVectorizer와 TfidfTransformer를 사용하여 증상 벡터화
cv = CountVectorizer()
tfidf = TfidfTransformer()

symptoms = token_disease['토큰키워드'].values
symptom_vectors = cv.fit_transform(symptoms)
symptom_tfidf = tfidf.fit_transform(symptom_vectors)

# 다항 로지스틱 회귀 분석 모델 학습
model = RandomForestClassifier()
model.fit(symptom_tfidf, token_disease['질병명'])

# 사용자로부터 증상 입력 받기
question = input("증상을 입력하세요 : ")

# 입력된 증상을 토큰화하고 정규화하여 예측에 사용
t = Okt()
q_list = [token for token, pos in t.pos(question, stem=True, norm=True) if pos in ['Noun', 'Adjective', 'Adverb']]
qustion_key_list = [lk for lk in list(set(q_list)) if lk not in stopword and len(lk) > 1]
#print(qustion_key_list)
user_vector = cv.transform([' '.join(qustion_key_list)])
user_tfidf = tfidf.transform(user_vector)

# 다항 로지스틱 회귀 분석 모델을 사용하여 질병 예측
predicted_probabilities = model.predict_proba(user_tfidf)[0]

# 상위 10개의 질병 출력
top_10_indices = np.argsort(predicted_probabilities)[::-1][:10]
print('상위 10개의 질병:')
for i, index in enumerate(top_10_indices):
    print(f'{i+1}. {model.classes_[index]} ({predicted_probabilities[index]:.4f})')  # ({predicted_probabilities[index]:.4f})

상위 10개의 질병:
1. 메니에르병(Meniere's disease) (0.0400)
2. 냉방병(Air-conditioningitis) (0.0300)
3. 비립종(Milium) (0.0300)
4. 급성 간질성 신염(Acute tubulo-interstitial nephritis) (0.0200)
5. 침샘염(Sialoadenitis) (0.0200)
6. 편도결석(tonsillolith) (0.0200)
7. 경골과 비골 골절(Fracture of tibia & fibula) (0.0200)
8. 요충증(Enterobiasis) (0.0200)
9. 폐렴(Pneumonia) (0.0200)
10. 아킬레스 건 파열(Acute achilles tendon rupture) (0.0200)


In [24]:
# 입력된 증상을 토큰화하고 정규화하여 예측에 사용
question = input("질문을 입력하세요 : ")
q_list = [token for token, pos in t.pos(question, stem=True, norm=True) if pos in ['Noun', 'Adjective', 'Adverb']]
qustion_key_list = [lk for lk in list(set(q_list)) if lk not in stopword and len(lk) > 1]
print(qustion_key_list)

#q_list = []
#for token, pos in t.pos(q_list, stem=True, norm=True):
#    if pos in ['Noun', 'Adjective', 'Adverb']:  # 명사, 형용사, 부사인 것 만 추출
#        q_list.append(token)

#print(list(set(keyword)))
#key_list = []
#for lk in list(set(keyword)):
#    if lk not in stopword:
#        key_list.append(lk)
#print(key_list)

['심하다', '근육통', '관절']


In [17]:
#from soynlp import DoublespaceLineCorpus
from soynlp.word import WordExtractor
from soynlp.tokenizer import LTokenizer
from soynlp.tokenizer import MaxScoreTokenizer

In [19]:
#corpus = DoublespaceLineCorpus(disease1['키워드'][0])

word_extractor = WordExtractor()
word_extractor.train(disease1['키워드'][0])
word_score_table = word_extractor.extract()

training was done. used memory 0.388 Gby 0.361 Gb
all cohesion probabilities was computed. # words = 6123
all branching entropies was computed # words = 10182
all accessor variety was computed # words = 10182


In [21]:
scores = {word:score.cohesion_forward for word, score in word_score_table.items()}
#scores
l_tokenizer = LTokenizer(scores = scores)
l_tokenizer.tokenize("머리가 아프고, 배도 아파요", flatten=False)

[('머리', '가'), ('아프고', ','), ('배도', ''), ('아파요', '')]

In [3]:
disease1 = disease.iloc[:, [0,1,]]
disease1.head()

질병명   
0                       근감소증(Sarcopenia)  \
1                       코로나-19(COVID-19)   
2  용혈성 요독 증후군(Hemolytic Uremic Syndrome)   
3                  단순 포진(Herpes Simplex)   
4                   약물 발진(Drug Eruption)   

                                               증상키워드  
0                         보행이상, 근력 약화, 피로감, 하지의 근력약화  
1               가래, 기침, 목의 통증, 근육통, 피로감, 열, 두통, 호흡곤란  
2  멍, 빈혈, 열, 황달, 혈뇨, 신부전, 전신 부종, 간비대, 복부 통증, 자반증,...  
3                                       작열감, 물집, 소양감  
4                                                 발진

In [5]:
count_vec = pd.read_csv("count_vec.csv")
count_vec.head()

질병명  6개  o자  w모양  x자  가늘어지는  가늘어짐  가래   
0                       근감소증(Sarcopenia)   0   0    0   0      0     0   0  \
1                       코로나-19(COVID-19)   0   0    0   0      0     0   1   
2  용혈성 요독 증후군(Hemolytic Uremic Syndrome)   0   0    0   0      0     0   0   
3                  단순 포진(Herpes Simplex)   0   0    0   0      0     0   0   
4                   약물 발진(Drug Eruption)   0   0    0   0      0     0   0   

   가슴  각막  ...  흉수  흑색변  흔들거림  흔들림  흡수장애  흥분  희발월경  흰빛으로  힘듬  힘이  
0   0   0  ...   0    0     0    0     0   0     0     0   0   0  
1   0   0  ...   0    0     0    0     0   0     0     0   0   0  
2   0   0  ...   0    0     0    0     0   0     0     0   0   0  
3   0   0  ...   0    0     0    0     0   0     0     0   0   0  
4   0   0  ...   0    0     0    0     0   0     0     0   0   0  

[5 rows x 739 columns]